In [1]:
from __future__ import division

import pandas as pd
import numpy as np

import bokeh.plotting as bkP
import bokeh.models as bkM
from bokeh.palettes import Spectral6
from bokeh.embed import file_html
from bokeh.resources import CDN

bkP.output_notebook()
from bokeh.io import push_notebook


/Users/diaz/anaconda/lib/python2.7/site-packages/pandas/computation/__init__.py:19: UserWarning: The installed version of numexpr 2.4.4 is not supported in pandas and will be not be used

  UserWarning)


Loading BokehJS ...

### Glyphs

In [2]:
initRectGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.6,
            fill_color='gray')

undefinedGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.3,
            fill_color='gray')

selectedGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.3,
            fill_color='yellow')

usSaccadeGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.3,
            fill_color='green')

usFixationGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.3,
            fill_color='red')

sSaccadeGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=.8,
            fill_color='green')

sFixationGlyph = bkM.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.8,
            fill_color='red')




### Data sources and JS callbacks

In [3]:
undefinedSource = bkM.ColumnDataSource(data=dict(x=[], y=[], width=[], height=[],leftEdge=[],rightEdge=[],boxID =[]))
fixSource = bkM.ColumnDataSource(data=dict(x=[], y=[], width=[], height=[],leftEdge=[],rightEdge=[],boxID =[]))
saccSource = bkM.ColumnDataSource(data=dict(x=[], y=[], width=[], height=[],leftEdge=[],rightEdge=[],boxID =[]))

# Every box has a custom numerical ID
boxCounter = 0

boxCallback = bkM.CustomJS(args=dict(), code="""

        /// get BoxSelectTool dimensions from cb_data parameter of Callback
        var geometry = cb_data['geometry'];

        /// calculate Rect attributes
        var width = geometry['x1'] - geometry['x0'];
        var height = geometry['y1'] - geometry['y0'];
        var x = geometry['x0'] + width/2;
        var y = geometry['y0'] + height/2;
        
        var leftEdge = geometry['x0']
        var rightEdge = geometry['x1']
        
        var k = IPython.notebook.kernel
        
        k.execute("undefinedSource.data[\'x\'].append(" + x + ")");
        k.execute("undefinedSource.data[\'y\'].append(" + y + ")");
        k.execute("undefinedSource.data[\'width\'].append(" + width + ")");
        k.execute("undefinedSource.data[\'height\'].append(" + height + ")");
        k.execute("undefinedSource.data[\'leftEdge\'].append(" + leftEdge + ")");
        k.execute("undefinedSource.data[\'rightEdge\'].append(" + rightEdge + ")");
        k.execute("undefinedSource.data[\'rightEdge\'].append(" + rightEdge + ")");
        k.execute("undefinedSource.data[\'boxID\'].append(boxCounter)");
        k.execute("boxCounter += 1");
        
        k.execute("push_notebook()");

    """)

selectedID = False

boxIds = [] 
idx = []

# I need the boxID of the selected object
tapCallback = bkM.CustomJS(args=dict(source = undefinedSource,fS=fixSource, sS=saccSource), code="""
        
        var idx = cb_obj.get('selected')['1d'].indices[0];
        var data = cb_obj[]
    
        /// How do I get the boxID field of the selected item's source?
        
        k.execute("selectedID = " + data );
        
    """)




    
    
#var idOfTapped = cb_obj.get('data')['boxID']
#k.execute("selectedID = " + idOfTapped );
#        var boxIds = cb_obj.get('data')['boxID']

#var boxIds = cb_obj.get('data')['boxID']

### Callbacks for ipywidgets

In [4]:
from ipywidgets import *
from IPython.display import display

def removeBox(sender):
    global selectedID
    for key,values in boxSource.data.iteritems():
        del values[boxSource.data['boxID'].index(selectedID)]
    
def moveBetweenSources(currSource,newSource):    

    global selectedID
    for key,values in currSource.data.iteritems():
        
        # Get the index of the selected item in currSource
        valueIdx = currSource.data['boxID'].index(selectedID)
        
        # print currSource.data[key][valueIdx]
        newSource.data[key].append( currSource.data[key][valueIdx] )
        del values[valueIdx]
        
    return newSource

def foundSacc(sender):
    
    # This assumes that data for the selected event belongs to undefinedSource.
    # This may not be the case.
    global saccSource
    saccSource = moveBetweenSources(undefinedSource,saccSource)
    
    

### The figure

In [5]:
leftEdge = []
rightEdge = []

p = bkP.figure(width=800, height=350,x_range=[0,13], y_range=(0,2))

x = np.deg2rad(range(720))
y = 1+np.sin(x)

p.xaxis.axis_label = 'time'
p.yaxis.axis_label = 'position'

p.line(x,y,line_width=4,name='aLine')

undefinedSelectionGlyph = p.add_glyph(undefinedSource, initRectGlyph, 
                             selection_glyph= selectedGlyph, 
                             nonselection_glyph= undefinedGlyph,
                             name='undefined')

fixSelectionGlyph = p.add_glyph(fixSource, initRectGlyph, 
                             selection_glyph=sFixationGlyph, 
                             nonselection_glyph=usFixationGlyph,
                             name='fixation')

p.add_tools(bkM.BoxSelectTool(dimensions=["width"],callback=boxCallback))
p.add_tools(bkM.TapTool())

bkP.show(p)


In [8]:
b1 = Button(description='Mark as saccade',value=False)
b1.on_click(foundSacc)
b1.width = '20%'

b2 = Button(description='Remove event',value=False)
b2.on_click(removeBox)
b2.width = '20%'

display(b1,b2)